In [1]:
import os 
import datetime
import numpy as np 
import pandas as pd 
import vectorbt as vbt 

In [2]:
end_date = datetime.datetime.now()
start_date = end_date - datetime.timedelta(days = 3)

In [4]:
btc_price = vbt.YFData.download(
    ["BTC-USD", "JPM"],
    interval = "1m",
    start = start_date,
    end = end_date,    
    missing_index="drop").get("Close")


c:\Users\User\.conda\envs\pytorch\Lib\site-packages\vectorbt\data\base.py:527: UserWarning: Symbols have mismatching index. Dropping missing data points.
  data = cls.align_index(data, missing=missing_index)


In [4]:
print(type(btc_price))

<class 'pandas.core.series.Series'>


In [5]:
btc_price

symbol                          BTC-USD         JPM
Datetime                                           
2024-06-17 13:30:00+00:00  65640.906250  193.399994
2024-06-17 13:31:00+00:00  65582.867188  193.050003
2024-06-17 13:32:00+00:00  65516.191406  192.910004
2024-06-17 13:33:00+00:00  65429.964844  192.841507
2024-06-17 13:35:00+00:00  65397.476562  193.899994
...                                 ...         ...
2024-06-18 19:27:00+00:00  64557.816406  196.940002
2024-06-18 19:29:00+00:00  64520.152344  196.844498
2024-06-18 19:30:00+00:00  64533.328125  196.867004
2024-06-18 19:31:00+00:00  64487.941406  196.880005
2024-06-18 19:32:00+00:00  64512.566406  196.839996

[629 rows x 2 columns]

In [6]:
rsi = vbt.RSI.run(btc_price, window = 14)

print(rsi.rsi)

Datetime
2024-06-11 12:11:00+00:00          NaN
2024-06-11 12:12:00+00:00          NaN
2024-06-11 12:13:00+00:00          NaN
2024-06-11 12:14:00+00:00          NaN
2024-06-11 12:15:00+00:00          NaN
                               ...    
2024-06-14 12:00:00+00:00    54.898330
2024-06-14 12:02:00+00:00    42.099416
2024-06-14 12:03:00+00:00    47.403030
2024-06-14 12:05:00+00:00    29.848889
2024-06-14 12:06:00+00:00    50.829556
Name: (14, Close), Length: 3697, dtype: float64


In [8]:
entries = rsi.rsi_crossed_below(30)
exits = rsi.rsi_crossed_above(70)
print(entries.to_string()) 
## or 
print(entries)

Datetime
2024-06-11 12:11:00+00:00    False
2024-06-11 12:12:00+00:00    False
2024-06-11 12:13:00+00:00    False
2024-06-11 12:14:00+00:00    False
2024-06-11 12:15:00+00:00    False
2024-06-11 12:17:00+00:00    False
2024-06-11 12:18:00+00:00    False
2024-06-11 12:19:00+00:00    False
2024-06-11 12:20:00+00:00    False
2024-06-11 12:21:00+00:00    False
2024-06-11 12:23:00+00:00    False
2024-06-11 12:24:00+00:00    False
2024-06-11 12:26:00+00:00    False
2024-06-11 12:27:00+00:00    False
2024-06-11 12:28:00+00:00    False
2024-06-11 12:29:00+00:00     True
2024-06-11 12:30:00+00:00    False
2024-06-11 12:31:00+00:00    False
2024-06-11 12:32:00+00:00    False
2024-06-11 12:33:00+00:00    False
2024-06-11 12:34:00+00:00    False
2024-06-11 12:35:00+00:00    False
2024-06-11 12:36:00+00:00    False
2024-06-11 12:37:00+00:00    False
2024-06-11 12:38:00+00:00    False
2024-06-11 12:39:00+00:00     True
2024-06-11 12:40:00+00:00    False
2024-06-11 12:41:00+00:00    False
2024-06-11 

In [32]:
pf = vbt.Portfolio.from_signals(btc_price, entries, exits,freq="1m" )
print(pf.stats())

Start                         2024-06-09 11:08:00+00:00
End                           2024-06-12 11:04:00+00:00
Period                                  2 days 16:06:00
Start Value                                       100.0
End Value                                     99.531293
Total Return [%]                              -0.468707
Benchmark Return [%]                          -2.041199
Max Gross Exposure [%]                            100.0
Total Fees Paid                                     0.0
Max Drawdown [%]                               2.805344
Max Drawdown Duration                   1 days 11:28:00
Total Trades                                         63
Total Closed Trades                                  63
Total Open Trades                                     0
Open Trade PnL                                      0.0
Win Rate [%]                                  58.730159
Best Trade [%]                                 0.458129
Worst Trade [%]                               -1

In [33]:
print(pf.total_return())

-0.004687073366422112


In [34]:
pf.plot().show()

### CREATING CUSTOM INDICATORS ###

In [35]:
print(btc_price)

Datetime
2024-06-09 11:08:00+00:00    69351.093750
2024-06-09 11:09:00+00:00    69352.992188
2024-06-09 11:11:00+00:00    69344.265625
2024-06-09 11:12:00+00:00    69341.882812
2024-06-09 11:14:00+00:00    69345.976562
                                 ...     
2024-06-12 10:59:00+00:00    68000.656250
2024-06-12 11:00:00+00:00    67988.898438
2024-06-12 11:02:00+00:00    67962.492188
2024-06-12 11:03:00+00:00    67957.335938
2024-06-12 11:04:00+00:00    67935.500000
Name: Close, Length: 3846, dtype: float64


In [36]:
def custom_indicator(close, rsi_window = 14, ma_window = 50, entry = 30, exit = 70):
    rsi = vbt.RSI.run(close, window= rsi_window).rsi.to_numpy()
    ma = vbt.MA.run(close, ma_window).ma.to_numpy()
    trend = np.where(rsi > exit, -1, 0)
    trend = np.where((rsi < entry) & (close < ma), 1, trend)
    
    return trend

ind = vbt.IndicatorFactory(class_name=  "Combination",
                           short_name=  "comb",
                           input_names = ["close"],
                           param_names = ['rsi_window', 'ma_window', 'entry', 'exit'],
                           output_names=['value']).from_apply_func(custom_indicator, 
                                                                   rsi_window = 14, 
                                                                   ma_window = 50,
                                                                   entry = 30,
                                                                   exit = 70,
                                                                   keep_pd = True)

res = ind.run(btc_price, 
              rsi_window = [14,35,21], 
              ma_window = [21,50, 100],
              entry = [30,40],
              exit = [70,60],
              param_product = True)

print(res.value)

entries = res.value == 1.0
exits = res.value == -1.0

comb_rsi_window            14                               ...  21            \
comb_ma_window            21           50           100     ... 21     50       
comb_entry                 30    40     30    40     30     ...  40     30      
comb_exit                  70 60 70 60  70 60 70 60  70 60  ...  70 60  70 60   
Datetime                                                    ...                 
2024-06-09 11:08:00+00:00   0  0  0  0   0  0  0  0   0  0  ...   0  0   0  0   
2024-06-09 11:09:00+00:00   0  0  0  0   0  0  0  0   0  0  ...   0  0   0  0   
2024-06-09 11:11:00+00:00   0  0  0  0   0  0  0  0   0  0  ...   0  0   0  0   
2024-06-09 11:12:00+00:00   0  0  0  0   0  0  0  0   0  0  ...   0  0   0  0   
2024-06-09 11:14:00+00:00   0  0  0  0   0  0  0  0   0  0  ...   0  0   0  0   
...                        .. .. .. ..  .. .. .. ..  .. ..  ...  .. ..  .. ..   
2024-06-12 10:59:00+00:00  -1 -1 -1 -1  -1 -1 -1 -1  -1 -1  ...  -1 -1  -1 -1   
2024-06-12 11:00:00+00:00  -

In [37]:
pf = vbt.Portfolio.from_signals(btc_price, entries, exits, freq= "1m")

print(pf.stats())

Start                         2024-06-09 11:08:00+00:00
End                           2024-06-12 11:04:00+00:00
Period                                  2 days 16:06:00
Start Value                                       100.0
End Value                                     99.128663
Total Return [%]                              -0.871337
Benchmark Return [%]                          -2.041199
Max Gross Exposure [%]                            100.0
Total Fees Paid                                     0.0
Max Drawdown [%]                               3.290992
Max Drawdown Duration                   1 days 11:45:50
Total Trades                                  43.888889
Total Closed Trades                           43.861111
Total Open Trades                              0.027778
Open Trade PnL                                  0.00307
Win Rate [%]                                  57.316232
Best Trade [%]                                 0.460574
Worst Trade [%]                               -1

C:\Users\User\AppData\Local\Temp\ipykernel_21408\2660161974.py:3: UserWarning:

Object has multiple columns. Aggregating using <function mean at 0x000001E4396C7D80>. Pass column to select a single column/group.



### HYPERPARAMETER OPTIMIZATION ###

You do not run this as it will aggregate the columns and you will not get a clear picture

pf = vbt.Portfolio.from_signals(btc_price, entries, exits, freq= "1m")

print(pf.stats())


Provide list of values or numpy arrays to create to the input functions and VectorBT will automatically backtests them.  

In [38]:
pf = vbt.Portfolio.from_signals(btc_price, entries, exits, freq= "1m")

print(pf.total_return())

comb_rsi_window  comb_ma_window  comb_entry  comb_exit
14               21              30          70          -0.004093
                                             60          -0.002846
                                 40          70          -0.021206
                                             60          -0.021687
                 50              30          70          -0.004245
                                             60          -0.002248
                                 40          70          -0.010067
                                             60          -0.010287
                 100             30          70          -0.000921
                                             60          -0.001617
                                 40          70          -0.015633
                                             60          -0.015132
35               21              30          70          -0.026131
                                             60           0.000798
       

In [39]:
returns = pf.total_return()

"""returns = returns[returns.index.isin(['ETH-USD'], level = "symbol")]"""
#returns = returns.groupby(level = ['comb_exit', 'comb_entry']).mean()


print(returns.to_string())
print(returns.max())
print(returns.idxmax())

comb_rsi_window  comb_ma_window  comb_entry  comb_exit
14               21              30          70          -0.004093
                                             60          -0.002846
                                 40          70          -0.021206
                                             60          -0.021687
                 50              30          70          -0.004245
                                             60          -0.002248
                                 40          70          -0.010067
                                             60          -0.010287
                 100             30          70          -0.000921
                                             60          -0.001617
                                 40          70          -0.015633
                                             60          -0.015132
35               21              30          70          -0.026131
                                             60           0.000798
       

In [ ]:
#"comb_rsi_window ,comb_ma_window "

fig = returns.vbt.heatmap(x_level = "comb_exit",
                          y_level = "comb_entry",
                          slider_level = "symbol")

fig.show()

### OPTIMIZATION TECHNIQUES ###

For more info check SuperFast SuperTrend on the docs page

In [40]:
import talib ### low level C cide
from numba import njit

In [41]:
RSI = vbt.IndicatorFactory.from_talib("RSI")

@njit # Numba decorators to speed up code 
def produce_signal(rsi, entry, exit):
    trend = np.where(rsi > exit, -1, 0)
    trend = np.where((rsi < entry), 1, trend)
    return trend

def custom_indicator(close, rsi_window = 14, entry = 30, exit = 70):
    rsi = RSI.run(close, rsi_window).real.to_numpy()
    return produce_signal(rsi, entry, exit)

ind = vbt.IndicatorFactory(class_name=  "Combination",
                           short_name=  "comb",
                           input_names = ["close"],
                           param_names = ['rsi_window', 'entry', 'exit'],
                           output_names=['value']).from_apply_func(custom_indicator, 
                                                                   rsi_window = 14, 
                                                                   entry = 30,
                                                                   exit = 70
                                                                   )

res = ind.run(btc_price, 
              rsi_window = np.arange(10,40,step = 3, dtype = int), 
              entry = np.arange(10,40, step = 2, dtype = int),
              exit = np.arange(60, 85, step = 2, dtype = int),
              param_product = True)

print(res.value)

entries = res.value == 1.0
exits = res.value == -1.0

comb_rsi_window           10                             ... 37              \
comb_entry                10                             ... 38               
comb_exit                 60 62 64 66 68 70 72 74 76 78  ... 66 68 70 72 74   
Datetime                                                 ...                  
2024-06-09 11:08:00+00:00  0  0  0  0  0  0  0  0  0  0  ...  0  0  0  0  0   
2024-06-09 11:09:00+00:00  0  0  0  0  0  0  0  0  0  0  ...  0  0  0  0  0   
2024-06-09 11:11:00+00:00  0  0  0  0  0  0  0  0  0  0  ...  0  0  0  0  0   
2024-06-09 11:12:00+00:00  0  0  0  0  0  0  0  0  0  0  ...  0  0  0  0  0   
2024-06-09 11:14:00+00:00  0  0  0  0  0  0  0  0  0  0  ...  0  0  0  0  0   
...                       .. .. .. .. .. .. .. .. .. ..  ... .. .. .. .. ..   
2024-06-12 10:59:00+00:00 -1 -1 -1 -1 -1 -1 -1 -1 -1  0  ... -1  0  0  0  0   
2024-06-12 11:00:00+00:00 -1 -1 -1 -1 -1 -1  0  0  0  0  ...  0  0  0  0  0   
2024-06-12 11:02:00+00:00 -1  0  0  0  0  0  0  0  0

### GRAPHING / DASHBOARDING ###

pf.trades
pf.orders

##### if you use .records_arr with the above you can extract the raw data from traders/orders to plot in a separate lib  

In [62]:
## You need to check the documentation on vectorbt.com to check for data that you want to obtain from the portfolio with trades method and then the specic data 
pf.trades.records_arr

array([(   0,  0, 0.00143588,  104, 69643.78125  , 0.,  135, 69451.6953125, 0., -0.27581205, -0.00275812, 0, 1,    0),
       (   1,  0, 0.00143783,  172, 69357.2109375, 0.,  186, 69444.2421875, 0.,  0.12513653,  0.00125483, 0, 1,    1),
       (   2,  0, 0.00143777,  226, 69447.25     , 0.,  240, 69524.484375 , 0.,  0.11104544,  0.00111213, 0, 1,    2),
       ...,
       (1577, 35, 0.0014883 , 3530, 67443.453125 , 0., 3594, 67317.3671875, 0., -0.18765387, -0.00186951, 0, 1, 1577),
       (1578, 35, 0.00148909, 3628, 67281.71875  , 0., 3652, 67326.4765625, 0.,  0.06664841,  0.00066523, 0, 1, 1578),
       (1579, 35, 0.00148857, 3741, 67349.9921875, 0., 3750, 67476.3515625, 0.,  0.18809477,  0.00187616, 0, 1, 1579)],
      dtype={'names': ['id', 'col', 'size', 'entry_idx', 'entry_price', 'entry_fees', 'exit_idx', 'exit_price', 'exit_fees', 'pnl', 'return', 'direction', 'status', 'parent_id'], 'formats': ['<i4', '<i4', '<f8', '<i4', '<f8', '<f8', '<i4', '<f8', '<f8', '<f8', '<f8', '<i4'

In [50]:
dir(pf.trades)

['__annotations__',
 '__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__getitem__',
 '__getstate__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__len__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_close',
 '_col_mapper',
 '_config',
 '_field_config',
 '_iloc',
 '_indexing_kwargs',
 '_loc',
 '_metrics',
 '_records_arr',
 '_subplots',
 '_ts',
 '_wrapper',
 'apply',
 'apply_mask',
 'avg_duration',
 'build_field_config_doc',
 'build_metrics_doc',
 'build_subplots_doc',
 'close',
 'closed',
 'col',
 'col_arr',
 'col_mapper',
 'config',
 'copy',
 'count',
 'coverage',
 'deep_getattr',
 'direction',
 'dumps',
 'duration',
 'end_idx',
 'entry_fees',
 'entry_idx',
 'entry_price',
 'exit_fees',
 'exit_idx',
 'exit_price',
 'expectancy',
 'field_config',
 'fro

In [71]:
pf.trades.records_arr

array([(   0,  0, 0.00143588,  104, 69643.78125  , 0.,  135, 69451.6953125, 0., -0.27581205, -0.00275812, 0, 1,    0),
       (   1,  0, 0.00143783,  172, 69357.2109375, 0.,  186, 69444.2421875, 0.,  0.12513653,  0.00125483, 0, 1,    1),
       (   2,  0, 0.00143777,  226, 69447.25     , 0.,  240, 69524.484375 , 0.,  0.11104544,  0.00111213, 0, 1,    2),
       ...,
       (1577, 35, 0.0014883 , 3530, 67443.453125 , 0., 3594, 67317.3671875, 0., -0.18765387, -0.00186951, 0, 1, 1577),
       (1578, 35, 0.00148909, 3628, 67281.71875  , 0., 3652, 67326.4765625, 0.,  0.06664841,  0.00066523, 0, 1, 1578),
       (1579, 35, 0.00148857, 3741, 67349.9921875, 0., 3750, 67476.3515625, 0.,  0.18809477,  0.00187616, 0, 1, 1579)],
      dtype={'names': ['id', 'col', 'size', 'entry_idx', 'entry_price', 'entry_fees', 'exit_idx', 'exit_price', 'exit_fees', 'pnl', 'return', 'direction', 'status', 'parent_id'], 'formats': ['<i4', '<i4', '<f8', '<i4', '<f8', '<f8', '<i4', '<f8', '<f8', '<f8', '<f8', '<i4'

In [59]:
pf.orders.records_readable

Order Id             Column                 Timestamp      Size  \
0            0   (14, 21, 30, 70) 2024-06-09 13:15:00+00:00  0.001436   
1            1   (14, 21, 30, 70) 2024-06-09 13:48:00+00:00  0.001436   
2            2   (14, 21, 30, 70) 2024-06-09 14:29:00+00:00  0.001438   
3            3   (14, 21, 30, 70) 2024-06-09 14:45:00+00:00  0.001438   
4            4   (14, 21, 30, 70) 2024-06-09 15:27:00+00:00  0.001438   
...        ...                ...                       ...       ...   
3154      3154  (21, 100, 40, 60) 2024-06-12 06:11:00+00:00  0.001488   
3155      3155  (21, 100, 40, 60) 2024-06-12 06:49:00+00:00  0.001489   
3156      3156  (21, 100, 40, 60) 2024-06-12 07:17:00+00:00  0.001489   
3157      3157  (21, 100, 40, 60) 2024-06-12 09:03:00+00:00  0.001489   
3158      3158  (21, 100, 40, 60) 2024-06-12 09:14:00+00:00  0.001489   

             Price  Fees  Side  
0     69643.781250   0.0   Buy  
1     69451.695312   0.0  Sell  
2     69357.210938   0.0   Buy  
3     69444.242188   0.0  Sell  
4     69447.250000   0.0   Buy  
...            ...   ...   ...  
3154  67317.367188   0.0  Sell  
3155  67281.718750   0.0   Buy  
3156  67326.476562   0.0  Sell  
3157  67349.992188   0.0   Buy  
3158  67476.351562   0.0  Sell  

[3159 rows x 7 columns]

In [61]:
pf.orders.records_arr  ### Exctracts the orders array from the portfolio object 

array([(   0,  0,  104, 0.00143588, 69643.78125  , 0., 0),
       (   1,  0,  135, 0.00143588, 69451.6953125, 0., 1),
       (   2,  0,  172, 0.00143783, 69357.2109375, 0., 0), ...,
       (3156, 35, 3652, 0.00148909, 67326.4765625, 0., 1),
       (3157, 35, 3741, 0.00148857, 67349.9921875, 0., 0),
       (3158, 35, 3750, 0.00148857, 67476.3515625, 0., 1)],
      dtype={'names': ['id', 'col', 'idx', 'size', 'price', 'fees', 'side'], 'formats': ['<i4', '<i4', '<i4', '<f8', '<f8', '<f8', '<i4'], 'offsets': [0, 4, 8, 16, 24, 32, 40], 'itemsize': 48, 'aligned': True})

In [75]:
vbt.settings.set_theme('dark')
vbt.settings['plotting']['layout']['width'] = 900
vbt.settings['plotting']['layout']['height'] = 450

fig = btc_price.vbt.plot(trace_kwargs = dict(name = 'Price'))
fig.show()

In [79]:
fig = pf.plot(subplots= [
    'orders',
    'trade_pnl',
    'cum_returns'
    ])

fig

C:\Users\User\AppData\Local\Temp\ipykernel_21408\1392903518.py:1: UserWarning:

Subplot 'orders' raised an exception



TypeError: Only one column is allowed. Use indexing or column argument.

### ORDER TYPES ###

pf.from_signals()


In [99]:
pf = vbt.Portfolio.from_signals(
    btc_price,
    entries,
    exits,
    sl_stop=0.005,
    sl_trail=True,
    tp_stop= 0.001,
    freq='1min',
    upon_stop_exit=vbt.portfolio.enums.StopExitMode.Reverse
)

pf.plot().show()

In [103]:
pf = vbt.Portfolio.from_signals(
    btc_price,
    short_exits=entries,
    short_entries=exits,
    freq='1min'
)



pf.plot().show()

In [104]:
pf.stats()

Start                         2024-06-09 11:08:00+00:00
End                           2024-06-12 11:07:00+00:00
Period                                  2 days 16:09:00
Start Value                                       100.0
End Value                                    101.661688
Total Return [%]                               1.661688
Benchmark Return [%]                          -2.099519
Max Gross Exposure [%]                            100.0
Total Fees Paid                                     0.0
Max Drawdown [%]                               1.664312
Max Drawdown Duration                   0 days 17:09:00
Total Trades                                         64
Total Closed Trades                                  63
Total Open Trades                                     1
Open Trade PnL                                 0.005006
Win Rate [%]                                  71.428571
Best Trade [%]                                 0.443155
Worst Trade [%]                               -0

### REALITY CHECK ###
-- avoiding overfitting

In [117]:
btc_price = vbt.YFData.download(
    'BTC-USD',
    missing_index='drop',
    interval = '1m',
    start = start_date,
    end = end_date
).get('Close')

btc_price

Datetime
2024-06-09 11:08:00+00:00    69351.093750
2024-06-09 11:09:00+00:00    69352.992188
2024-06-09 11:11:00+00:00    69344.265625
2024-06-09 11:12:00+00:00    69341.882812
2024-06-09 11:14:00+00:00    69345.976562
                                 ...     
2024-06-12 11:03:00+00:00    67957.335938
2024-06-12 11:04:00+00:00    67935.500000
2024-06-12 11:05:00+00:00    67913.875000
2024-06-12 11:06:00+00:00    67882.570312
2024-06-12 11:07:00+00:00    67895.054688
Name: Close, Length: 3849, dtype: float64

In [118]:
btc_price, range_indexes = btc_price.vbt.range_split(n=100, range_len = 1440)

In [119]:
def optimize_rsi(close, window, entry, exit):
    
    rsi = vbt.IndicatorFactory.from_talib('RSI').run(close, timeperiod = window).real
    return rsi < entry, rsi > exit


rsi_ind = vbt.IndicatorFactory(
    class_name='optimize_rsi',
    short_name='rsi',
    input_names=['close'],
    param_names=['window', 'entry', 'exit'],
    output_names=['entries', 'exits']
).from_apply_func(
    optimize_rsi,
    window = 14,
    entry = 30,
    exit = 70
)

step_size = 10
entries = np.arange(10,45, step = step_size, dtype = int)
exits = np.arange(55,95, step = step_size, dtype = int)
windows = np.arange(10,45, step = step_size, dtype = int)



In [120]:
rsi_res = rsi_ind.run(
    btc_price,
    window = windows,
    entry = entries,
    exit = exits,
    param_product = True
)

rsi_entries = rsi_res.entries
rsi_exits = rsi_res.exits

rsi_exits.iloc[-1, :] = True

rsi_pf = vbt.Portfolio.from_signals(btc_price, rsi_entries, rsi_exits, freq = '1T', fees = 0.0001)

fig = rsi_pf.total_return().vbt.volume(
    x_level = 'rsi_exit',
    y_level = 'rsi_entry',
    z_level = 'rsi_window',
    slider_level = 'split_idx'
)

fig.show()

In [121]:
fig = rsi_pf.total_return().vbt.heatmap(
    x_level = 'rsi_exit',
    y_level = 'rsi_entry',
    slider_level = 'split_idx'
)

fig.show()